In [1]:
!pip install -q scrapy


[notice] A new release of pip is available: 24.3.1 -> 25.0
[notice] To update, run: C:\Users\rebec\AppData\Local\Microsoft\WindowsApps\PythonSoftwareFoundation.Python.3.11_qbz5n2kfra8p0\python.exe -m pip install --upgrade pip


# Articulos de mapas de sitio usando scrapy

In [2]:
!scrapy startproject news_scraper

New Scrapy project 'news_scraper', using template directory 'C:\Users\rebec\AppData\Local\Packages\PythonSoftwareFoundation.Python.3.11_qbz5n2kfra8p0\LocalCache\local-packages\Python311\site-packages\scrapy\templates\project', created in:
    C:\Users\rebec\OneDrive - Universidad de Oviedo\Escritorio\TFG\news_scraper

You can start your first spider with:
    cd news_scraper
    scrapy genspider example example.com


## Mapas de sitio (XML)

In [3]:
%cd news_scraper

c:\Users\rebec\OneDrive - Universidad de Oviedo\Escritorio\TFG\news_scraper


In [4]:
%%writefile "sitemap_spider.py"
import scrapy
class SitemapSpider(scrapy.Spider):
    name = 'sitemap_spider'
    start_urls = ['https://www.elcomercio.es/sitemap.xml',
                  'https://www.lne.es/sitemap_google_news_52e19.xml',
                  'https://www.larazon.es/sitemaps/news.xml',
                  'https://www.lavanguardia.com/sitemap-google-news.xml',
                  'https://www.rtpa.es/sitemap-noticias.xml',
                  'https://www.europapress.es/news_sitemap_1.xml',
                  'https://www.abc.es/sitemap.xml',
                  'https://www.20minutos.es/sitemap-google-news.xml',
                  'https://www.elperiodico.com/es/google-news.xml',
                  'https://www.eldiario.es/sitemap_google_news_25b87.xml']
    #custom_settings = {
    #    'ROBOTSTXT_OBEY': False
    #}

    namespaces = {
        'ns': 'http://www.sitemaps.org/schemas/sitemap/0.9',  # Default namespace
        'news': 'http://www.google.com/schemas/sitemap-news/0.9'
    }

    def parse(self, response):
        # Extraer datos de cada tag <url>
        for url in response.xpath('//ns:url', namespaces=self.namespaces):
            loc = url.xpath('./ns:loc/text()', namespaces=self.namespaces).get()
            title = url.xpath('./news:news/news:title/text()', namespaces=self.namespaces).get()
            publication_date = url.xpath('./news:news/news:publication_date/text()', namespaces=self.namespaces).get()
            publisher = url.xpath('./news:news/news:publication/news:name/text()', namespaces=self.namespaces).get()

            yield {
                'fuente': publisher,
                'url': loc,
                'titulo': title,
                'fecha_publicacion': publication_date,
            }

Writing sitemap_spider.py


In [11]:
# !cp sitemap_spider.py news_scraper/spiders
! copy sitemap_spider.py news_scraper\spiders


        1 archivo(s) copiado(s).


In [14]:
!scrapy crawl sitemap_spider -o output.csv -s USER_AGENT="Mozilla/5.0 (Windows NT 10.0; Win64; x64) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/131.0.0.0 Safari/537.36 Edg/131.0.2903.70"
!scrapy crawl sitemap_spider -o news_output.csv

2025-02-04 21:21:19 [scrapy.utils.log] INFO: Scrapy 2.12.0 started (bot: news_scraper)
2025-02-04 21:21:19 [scrapy.utils.log] INFO: Versions: lxml 4.9.3.0, libxml2 2.10.3, cssselect 1.2.0, parsel 1.10.0, w3lib 2.3.1, Twisted 24.3.0, Python 3.11.9 (tags/v3.11.9:de54cf5, Apr  2 2024, 10:12:12) [MSC v.1938 64 bit (AMD64)], pyOpenSSL 25.0.0 (OpenSSL 3.3.2 3 Sep 2024), cryptography 43.0.3, Platform Windows-10-10.0.19045-SP0
2025-02-04 21:21:19 [scrapy.addons] INFO: Enabled addons:
[]
2025-02-04 21:21:19 [asyncio] DEBUG: Using selector: SelectSelector
2025-02-04 21:21:19 [scrapy.utils.log] DEBUG: Using reactor: twisted.internet.asyncioreactor.AsyncioSelectorReactor
2025-02-04 21:21:19 [scrapy.utils.log] DEBUG: Using asyncio event loop: asyncio.windows_events._WindowsSelectorEventLoop
2025-02-04 21:21:19 [scrapy.utils.log] DEBUG: Using reactor: twisted.internet.asyncioreactor.AsyncioSelectorReactor
2025-02-04 21:21:19 [scrapy.utils.log] DEBUG: Using asyncio event loop: asyncio.windows_events.

## Filtrar articulos por fecha

In [15]:
import pandas as pd

data_df = pd.read_csv("news_output.csv")
data_df['fecha_publicacion'] = pd.to_datetime(data_df['fecha_publicacion'], errors='coerce', utc=True)
data_df['fecha_publicacion'] = pd.to_datetime(data_df['fecha_publicacion'].dt.strftime("%Y-%m-%d"))
fecha_inicial = pd.Timestamp("2025-2-1")
data_df = data_df[data_df['fecha_publicacion'] >= fecha_inicial].drop_duplicates().reset_index(drop='True')
data_df

fuente                                                url  \
0     La Vanguardia  https://www.lavanguardia.com/magazine/bienesta...   
1     La Vanguardia  https://www.lavanguardia.com/deportes/futbol/2...   
2     La Vanguardia  https://www.lavanguardia.com/deportes/tenis/20...   
3     La Vanguardia  https://www.lavanguardia.com/television/202502...   
4     La Vanguardia  https://www.lavanguardia.com/participacion/las...   
...             ...                                                ...   
5757       La Razón  https://www.larazon.es/madrid/psoem-exhibe-obs...   
5758       La Razón  https://www.larazon.es/loteria/comprobar-dia-o...   
5759       La Razón  https://www.larazon.es/internacional/trump-rec...   
5760       La Razón  https://www.larazon.es/internacional/china-anu...   
5761       La Razón  https://www.larazon.es/cultura/arte/balad-beas...   

                                                 titulo fecha_publicacion  
0     Marian Rojas desvela las razones biológicas y ...        2025-02-04  
1     Alphonso Davies renueva con el Bayern y rechaz...        2025-02-04  
2      Simona Halep, ex número uno, anuncia su retirada        2025-02-04  
3     Máximo Huerta regresa este miércoles a 'El pro...        2025-02-04  
4               Cuando cae la noche en Whittington Park        2025-02-04  
...                                                 ...               ...  
5757  El PSOE-M exhibe su obsesión por Ayuso en su C...        2025-02-02  
5758  Comprobar Mi Día de la ONCE: resultado del sor...        2025-02-02  
5759  <![CDATA[Trump reconoce que la guerra comercia...        2025-02-02  
5760  China anuncia medidas para castigar a EEUU por...        2025-02-02  
5761  Balad Beast: el festival que está cambiando la...        2025-02-02  

[5762 rows x 4 columns]

In [16]:
# Articulos por fuente
data_df['fuente'].value_counts()

fuente
La Razón                           1034
Europa Press                       1000
La Vanguardia                       964
<![CDATA[El Periódico]]>            806
20minutos                           697
La Nueva España                     493
ElDiario.es                         445
El Comercio: Diario de Asturias     292
Vertele                              31
Name: count, dtype: int64

## Filtrar por palabras clave